In [22]:
from pathlib import Path
import pandas as pd
from dateutil.relativedelta import relativedelta
import plotly.express as px

ruta = Path(r"Z:\02_Maestría UNI\I_TALLER DE PROYECTOS II\EXPOSICION\expo2_akira\data\data.xlsx")
df = pd.read_excel(
    ruta, sheet_name="horizonte",
    parse_dates=["Inicio", "Fin"],
    engine="openpyxl"
).rename(columns=str.strip)

df.columns

Index(['Etapa', 'Inicio', 'Fin'], dtype='object')

In [24]:
import pandas as pd
import plotly.express as px
from dateutil.relativedelta import relativedelta

# ─── 2. DURACIÓN Y TEXTO ───────────────────────────────────
df['Duración'] = df.apply(
    lambda r: f"{relativedelta(r['Fin'], r['Inicio']).years}a "
              f"{relativedelta(r['Fin'], r['Inicio']).months}m "
              f"{relativedelta(r['Fin'], r['Inicio']).days}d", axis=1
)

df['texto_anotacion'] = "Fin: " + df['Fin'].dt.strftime("%d-%b-%Y")

# ─── 3. GRÁFICO ─────────────────────────────────────────────
fig = px.timeline(
    df.sort_values(by="Inicio"),
    x_start="Inicio",
    x_end="Fin",
    y="Etapa",
    color="Etapa",
    hover_data={"Duración": True, "Etapa": True, "Inicio": "|%d %B %Y", "Fin": "|%d %B %Y"},
    labels={"Etapa": "Etapa del Proyecto"},
)

fig.update_yaxes(showticklabels=False)

# ─── 4. POSICIÓN FINAL DE ANOTACIONES ──────────────────────
xmax = df["Fin"].max()

for i, row in df.iterrows():
    fig.add_annotation(
        x=xmax,
        y=row['Etapa'],
        text=row['texto_anotacion'],
        showarrow=False,
        font=dict(
            size=11,                # Tamaño de fuente
            color="white",
            family="Segoe UI"      # Tipo de letra
        ),
        xanchor="right",
        yanchor="middle",
        xshift=-5,
        bgcolor="rgba(50,50,50,0.7)",  # Fondo simulado (solo si usas `annotation`)
        borderpad=4
    )

# ─── 5. ESTILO ──────────────────────────────────────────────
fig.update_layout(
    title="HORIZONTE DE EVALUACIÓN DEL PROYECTO",
    title_x=0.5,
    autosize=True,
    yaxis_visible=False,
    height=None,  # ← evita height fijo
    margin=dict(t=60, r=20, l=40, b=40),
    plot_bgcolor="#0d1117",
    paper_bgcolor="#0d1117",
    font=dict(color="#c9d1d9"),
    legend_title_text='Etapas',
)
# ─── EXPORTACIÓN A HTML ───────────────────────────────────
fig.write_html(r"Z:\02_Maestría UNI\I_TALLER DE PROYECTOS II\EXPOSICION\expo2_akira\docs\plots\gantt_akirakato.html",
    full_html=True,
    include_plotlyjs="cdn",
    config={"responsive": True}
)
fig.show()


In [60]:
import pandas as pd
import plotly.graph_objects as go
from plotly.colors import qualitative, sequential
from pathlib import Path

# ─── PALETAS FIJAS PARA TODA LA TESIS ───────────────────────
PALETA_CATEGORICA = qualitative.Safe      # para categorías (etapas, niveles, regiones)
PALETA_NUMERICA   = sequential.Viridis    # para mapas, proporciones, ratios

# ─── 1. CARGA ────────────────────────────────────────────────
df = pd.read_excel(
    Path(r"Z:\02_Maestría UNI\I_TALLER DE PROYECTOS II\EXPOSICION\expo2_akira\data\data.xlsx"),
    sheet_name="demandacp"
)

# ─── 2. PIVOTEO Y ORDEN DE GRADOS ────────────────────────────
df["grado"] = df["grado"].astype(str) + "° grado"
orden = sorted(df["grado"].unique())
df_pivot = df.pivot(index="año", columns="grado", values="total").fillna(0)
df_pivot = df_pivot[orden]

# ─── 3. CENTRADO (CAMPANA) ───────────────────────────────────
totales = df_pivot.sum(axis=1)
bottoms = -totales / 2

# ─── 4. PALETA DE COLORES COHERENTE ──────────────────────────
color_map = {g: PALETA_CATEGORICA[i % len(PALETA_CATEGORICA)] for i, g in enumerate(orden)}

# ─── 5. CREACIÓN DEL GRÁFICO ─────────────────────────────────
fig = go.Figure()

for grado in orden:
    valores = df_pivot[grado]
    fig.add_bar(
        x=df_pivot.index,
        y=valores,
        base=bottoms,
        name=str(grado),
        marker_color=color_map[grado],
        text=valores,
        textposition="inside",
        textfont=dict(color="white", size=14)
    )
    bottoms += valores

# ─── 6. LÍNEAS VERTICALES POR AÑO ────────────────────────────
for año in df_pivot.index:
    fig.add_shape(
        type="line",
        x0=año, x1=año,
        y0=-totales.max() / 2,
        y1=totales.max() / 2,
        line=dict(color="rgba(255,255,255,0.1)", width=10),
        layer="below"
    )

# ─── 7. ESTILO GENERAL ───────────────────────────────────────
fig.update_layout(
    title="DEMANDA EFECTIVA CON PROYECTO - BRECHA A ATENDER",
    title_x=0.5,
    barmode="stack",
    xaxis=dict(tickmode='linear', dtick=1),
    yaxis_visible=False,
    xaxis_visible=True,
    yaxis_showticklabels=False,
    plot_bgcolor="#0d1117",
    paper_bgcolor="#0d1117",
    font=dict(color="#c9d1d9"),
    autosize=True,
    height=None,  # ← evita height fijo
    margin=dict(t=60, r=20, l=40, b=40),
    legend_title="Grado"
)

# ─── 8. EXPORTACIÓN A HTML ───────────────────────────────────
fig.write_html(r"Z:\02_Maestría UNI\I_TALLER DE PROYECTOS II\EXPOSICION\expo2_akira\docs\plots\demanda_efectiva_cp.html",
    full_html=True,
    include_plotlyjs="cdn",
    config={"responsive": True}
)

fig.show()


In [56]:
import plotly.graph_objects as go
import pandas as pd

# Datos de ejemplo
df = pd.DataFrame({
    'Factores': ['Secciones', 'Aulas (B+R+M)', 'Docentes', 'Directivos + Administrativos'],
    'Antes del Proyecto': [22, 11, 35, 5],
    'Después del Proyecto': [45, 25, 62, 20]
})

# Crear figura
fig = go.Figure()

# Agregar barra "Antes del Proyecto"
# Agregar barra "Después del Proyecto"
fig.add_bar(
    x=df['Factores'],
    y=df['Después del Proyecto'],
    name='Después del Proyecto',
    marker_color="#B85555",
    text=df['Después del Proyecto'],
    textposition='inside',
    opacity=0.7,
    width=0.8
)

fig.add_bar(
    x=df['Factores'],
    y=df['Antes del Proyecto'],
    name='Antes del Proyecto',
    marker_color="#4E3ED6",
    text=df['Antes del Proyecto'],
    textposition='inside',
    width=0.5
)



# Layout
fig.update_layout(
    barmode='overlay',
    title={
        'text': 'COMPARATIVO: FACTORES PRODUCTIVOS ANTES Y DESPUÉS DEL PROYECTO',
        'x': 0.5
    },
    xaxis_title='Factores',
    yaxis_title='Cantidad',
    legend_title_text='',
    yaxis_visible=False,
    xaxis_visible=True,
    yaxis_showticklabels=False,
    plot_bgcolor="#0d1117",
    paper_bgcolor="#0d1117",
    font=dict(color="#c9d1d9"),
    autosize=True,
    height=None,  # ← evita height fijo
    margin=dict(t=60, r=20, l=40, b=40),
    legend_title="Grado"
)

# Estilo de texto
fig.update_traces(textfont_size=14)
fig.write_html(r"Z:\02_Maestría UNI\I_TALLER DE PROYECTOS II\EXPOSICION\expo2_akira\docs\plots\antes_despues.html", full_html=True,
               include_plotlyjs="cdn",
               config={"responsive": True})
fig.show()


# DELITOS

In [3]:

# Delitos
import pandas as pd
delitos = pd.read_excel(r"Z:\06_BASES_DE_DATOS\01_DELITOS\02_MINISTERIO_INTERIOR\Base de datos SIDPOL a febrero del 2025.xlsx", sheet_name="Temp6")
delitos


ANIO  MES  UBIGEO_HECHO DPTO_HECHO_NEW   PROV_HECHO   DIST_HECHO  \
0       2024    1         10101       AMAZONAS  CHACHAPOYAS  CHACHAPOYAS   
1       2024    1         10101       AMAZONAS  CHACHAPOYAS  CHACHAPOYAS   
2       2024    1         10101       AMAZONAS  CHACHAPOYAS  CHACHAPOYAS   
3       2024    1         10101       AMAZONAS  CHACHAPOYAS  CHACHAPOYAS   
4       2024    1         10101       AMAZONAS  CHACHAPOYAS  CHACHAPOYAS   
...      ...  ...           ...            ...          ...          ...   
139179  2024   12        250304        UCAYALI   PADRE ABAD      NESHUYA   
139180  2024   12        250304        UCAYALI   PADRE ABAD      NESHUYA   
139181  2024   12        250304        UCAYALI   PADRE ABAD      NESHUYA   
139182  2024   12        250304        UCAYALI   PADRE ABAD      NESHUYA   
139183  2024   12        250401        UCAYALI        PURUS        PURUS   

                                       TIPO  \
0           ADMINISTRACION PUBLICA (DELITO)   
1           ADMINISTRACION PUBLICA (DELITO)   
2                         LIBERTAD (DELITO)   
3                         LIBERTAD (DELITO)   
4                         LIBERTAD (DELITO)   
...                                     ...   
139179                  PATRIMONIO (DELITO)   
139180                  PATRIMONIO (DELITO)   
139181  VIDA, EL CUERPO Y LA SALUD (DELITO)   
139182  VIDA, EL CUERPO Y LA SALUD (DELITO)   
139183  VIDA, EL CUERPO Y LA SALUD (DELITO)   

                                   SUB_TIPO  \
0                ADMINISTRACION DE JUSTICIA   
1       COMETIDOS POR FUNCIONARIOS PUBLICOS   
2                    VIOLACION DE DOMICILIO   
3         VIOLACION DE LA LIBERTAD PERSONAL   
4         VIOLACION DE LA LIBERTAD PERSONAL   
...                                     ...   
139179                                 ROBO   
139180                           USURPACION   
139181                            HOMICIDIO   
139182                             LESIONES   
139183                             LESIONES   

                                       MODALIDAD  n_dist_ID_DGC  
0       FUGA DEL LUGAR DEL ACCIDENTE DE TRANSITO              1  
1                        COHECHO ACTIVO GENERICO              1  
2                         VIOLACION DE DOMICILIO              1  
3                                          ACOSO              1  
4                                       COACCION              1  
...                                          ...            ...  
139179               ROBO AGRAVADO A MANO ARMADA              2  
139180                                USURPACION              1  
139181          HOMICIDIO CALIFICADO - ASESINATO              1  
139182                                  LESIONES              1  
139183                            LESIONES LEVES              2  

[139184 rows x 10 columns]

In [23]:
df = delitos.copy()
df["TIPO"].value_counts()
columnas = [
    "MES",
    "UBIGEO_HECHO",
    "DIST_HECHO",
    "TIPO",
    "n_dist_ID_DGC",
]
df = df[columnas].copy()
df


MES  UBIGEO_HECHO   DIST_HECHO                                 TIPO  \
0         1         10101  CHACHAPOYAS      ADMINISTRACION PUBLICA (DELITO)   
1         1         10101  CHACHAPOYAS      ADMINISTRACION PUBLICA (DELITO)   
2         1         10101  CHACHAPOYAS                    LIBERTAD (DELITO)   
3         1         10101  CHACHAPOYAS                    LIBERTAD (DELITO)   
4         1         10101  CHACHAPOYAS                    LIBERTAD (DELITO)   
...     ...           ...          ...                                  ...   
139179   12        250304      NESHUYA                  PATRIMONIO (DELITO)   
139180   12        250304      NESHUYA                  PATRIMONIO (DELITO)   
139181   12        250304      NESHUYA  VIDA, EL CUERPO Y LA SALUD (DELITO)   
139182   12        250304      NESHUYA  VIDA, EL CUERPO Y LA SALUD (DELITO)   
139183   12        250401        PURUS  VIDA, EL CUERPO Y LA SALUD (DELITO)   

        n_dist_ID_DGC  
0                   1  
1                   1  
2                   1  
3                   1  
4                   1  
...               ...  
139179              2  
139180              1  
139181              1  
139182              1  
139183              2  

[139184 rows x 5 columns]

In [24]:
# Seleccionar solo los delitos de interés según la columna "TIPO" con where
df2 = df[df["TIPO"].isin([
    "VIDA, EL CUERPO Y LA SALUD (DELITO)",
    "SEGURIDAD PUBLICA (DELITO)",
    "TRANQUILIDAD PUBLICA (DELITO)"
])].copy()

df2

MES  UBIGEO_HECHO   DIST_HECHO                                 TIPO  \
22        1         10101  CHACHAPOYAS           SEGURIDAD PUBLICA (DELITO)   
23        1         10101  CHACHAPOYAS           SEGURIDAD PUBLICA (DELITO)   
24        1         10101  CHACHAPOYAS  VIDA, EL CUERPO Y LA SALUD (DELITO)   
25        1         10101  CHACHAPOYAS  VIDA, EL CUERPO Y LA SALUD (DELITO)   
31        1         10108      HUANCAS           SEGURIDAD PUBLICA (DELITO)   
...     ...           ...          ...                                  ...   
139173   12        250303     CURIMANA  VIDA, EL CUERPO Y LA SALUD (DELITO)   
139174   12        250303     CURIMANA  VIDA, EL CUERPO Y LA SALUD (DELITO)   
139181   12        250304      NESHUYA  VIDA, EL CUERPO Y LA SALUD (DELITO)   
139182   12        250304      NESHUYA  VIDA, EL CUERPO Y LA SALUD (DELITO)   
139183   12        250401        PURUS  VIDA, EL CUERPO Y LA SALUD (DELITO)   

        n_dist_ID_DGC  
22                  3  
23                  1  
24                 15  
25                  2  
31                  1  
...               ...  
139173              1  
139174              1  
139181              1  
139182              1  
139183              2  

[32549 rows x 5 columns]

In [36]:
# Seleccionamos solo los distritros de la provincia de Lima
df2 = df2[df2["UBIGEO_HECHO"]//100 == 1501].copy()

df3 = df2.groupby(
    ["MES", "UBIGEO_HECHO", "DIST_HECHO"],
).agg(
    n_dist_ID_DGC=("n_dist_ID_DGC", "sum")
).reset_index()
df3

MES  UBIGEO_HECHO               DIST_HECHO  n_dist_ID_DGC
0      1        150101                     LIMA            301
1      1        150102                    ANCON             37
2      1        150103                      ATE            112
3      1        150104                 BARRANCO             35
4      1        150105                    BREÑA             20
..   ...           ...                      ...            ...
500   12        150139               SANTA ROSA              2
501   12        150140        SANTIAGO DE SURCO             60
502   12        150141                SURQUILLO             32
503   12        150142        VILLA EL SALVADOR             73
504   12        150143  VILLA MARIA DEL TRIUNFO            159

[505 rows x 4 columns]

In [ ]:
df3_por_distritos = df3.groupby("DIST_HECHO").agg(
    n_dist_ID_DGC=("n_dist_ID_DGC", "sum")
).reset_index()
df3_por_distritos.to_excel(r"C:\Users\SystemPeru\Downloads\delitos_por_distritos.xlsx", index=False)
df3_por_distritos


In [35]:
top10 = df3.groupby("DIST_HECHO")["n_dist_ID_DGC"].sum().nlargest(10).index
top10

Index(['SAN JUAN DE LURIGANCHO', 'LIMA', 'COMAS', 'VILLA MARIA DEL TRIUNFO',
       'ATE', 'SAN JUAN DE MIRAFLORES', 'SAN MARTIN DE PORRES', 'CHORRILLOS',
       'INDEPENDENCIA', 'CARABAYLLO'],
      dtype='object', name='DIST_HECHO')

In [69]:
df3_lima_top10 = df3[df3["DIST_HECHO"].isin(top10)].copy()
df3_lima_top10 = df3_lima_top10.sort_values(by=["DIST_HECHO", "MES"]).reset_index(drop=True)
df3_lima_top10
meses = {
    1: "Enero",
    2: "Febrero",
    3: "Marzo",
    4: "Abril",
    5: "Mayo",
    6: "Junio",
    7: "Julio",
    8: "Agosto",
    9: "Septiembre",
    10: "Octubre",
    11: "Noviembre",
    12: "Diciembre"
}
df3_lima_top10["MES_nombre"] = df3_lima_top10["MES"].map(meses)
df3_lima_top10

MES  UBIGEO_HECHO               DIST_HECHO  n_dist_ID_DGC  MES_nombre
0      1        150103                      ATE            112       Enero
1      2        150103                      ATE            148     Febrero
2      3        150103                      ATE            141       Marzo
3      4        150103                      ATE            112       Abril
4      5        150103                      ATE            156        Mayo
..   ...           ...                      ...            ...         ...
115    8        150143  VILLA MARIA DEL TRIUNFO            140      Agosto
116    9        150143  VILLA MARIA DEL TRIUNFO            134  Septiembre
117   10        150143  VILLA MARIA DEL TRIUNFO            128     Octubre
118   11        150143  VILLA MARIA DEL TRIUNFO            146   Noviembre
119   12        150143  VILLA MARIA DEL TRIUNFO            159   Diciembre

[120 rows x 5 columns]

In [71]:

df3_lima_top10["UBIGEO_HECHO"] = df3_lima_top10["UBIGEO_HECHO"].astype(str)
# Asegurar que el ubigeo tenga 6 dígitos
fig = px.density_heatmap(
    df3_lima_top10,
    y="DIST_HECHO",
    x="MES_nombre",
    z="n_dist_ID_DGC",
    color_continuous_scale=px.colors.sequential.Viridis,
    labels={"DIST_HECHO": "Distrito", "MES_nombre": "Mes", "n_dist_ID_DGC": "Número de Delitos"},
    title="Número de delitos por mes en el top 10 distritos de Lima",
    height=None,
    width=None,
)
fig.write_html(r"Z:\02_Maestría UNI\I_TALLER DE PROYECTOS II\EXPOSICION\expo2_akira\docs\plots\top10_delitos_mes.html",
    full_html=True,
    include_plotlyjs="cdn",
    config={"responsive": True}
)
fig.show()


In [50]:
df_2024_mes = df3.copy()
df_2024 = df3.groupby("UBIGEO_HECHO").agg({"n_dist_ID_DGC": "sum"}).reset_index()
df_2024


UBIGEO_HECHO  n_dist_ID_DGC
0         150101           2489
1         150102            387
2         150103           1719
3         150104            381
4         150105            207
5         150106           1250
6         150107            260
7         150108           1463
8         150109            134
9         150110           2486
10        150111            335
11        150112           1320
12        150113            191
13        150114            237
14        150115            706
15        150116            291
16        150117           1031
17        150118            998
18        150119            275
19        150120             97
20        150121            145
21        150122            501
22        150123            461
23        150124            121
24        150125           1207
25        150126             76
26        150127             31
27        150128            785
28        150129             42
29        150130            364
30        150131            170
31        150132           5765
32        150133           1617
33        150134            148
34        150135           1475
35        150136            257
36        150137            629
37        150138             17
38        150139             43
39        150140            887
40        150141            239
41        150142           1004
42        150143           1815

In [67]:

df_2024_Lima = df_2024[df_2024["UBIGEO_HECHO"]//100 == 1501].copy()
df_2024_Lima= df_2024_Lima.merge(
    delitos[["UBIGEO_HECHO", "DIST_HECHO"]],
    on="UBIGEO_HECHO",
    how="left",
).copy()
df_2024_Lima.drop_duplicates(subset=["UBIGEO_HECHO"], inplace=True)
df_2024_Lima

# Gráfico de barras ordenado por cantidad de delitos y solo mostrar los 10 primeros
df_2024_Lima = df_2024_Lima.sort_values(by="n_dist_ID_DGC", ascending=False).head(10)
# Gráfico de barras

fig = px.bar(
    df_2024_Lima,
    y="DIST_HECHO",
    x="n_dist_ID_DGC",
    color="DIST_HECHO",
    text="n_dist_ID_DGC",
    title="Delitos en Lima Metropolitana - 2024",
)
fig.update_traces(texttemplate='%{text:.2s}', textposition='outside')
fig.update_layout(
    yaxis_title="Distritos",
    xaxis_title="Cantidad de Delitos",
    plot_bgcolor="#0d1117",
    paper_bgcolor="#0d1117",
    font=dict(color="#c9d1d9"),
    autosize=True,
    height=None,  # ← evita height fijo
    margin=dict(t=60, r=20, l=40, b=40),
    #quitar leyenda
    showlegend=False,
)
# Añadir anotaciones fuente de datos en el gráfico
fig.add_annotation(
    text="Fuente: Ministerio del Interior - SIDPOL",
    xref="paper", yref="paper",
    x=1, y=-0.12,
    showarrow=False,
    font=dict(size=10, color="#c9d1d9"),
    bgcolor="#0d1117",
    bordercolor="#0d1117",
    borderwidth=1,
    borderpad=4
)

fig.show()

In [68]:
# Exportar a HTML sin ancho fijo y para incrustar en un sitio web
# Exportar a HTML sin ancho fijo y para incrustar en un sitio web
fig.write_html(r"Z:\02_Maestría UNI\I_TALLER DE PROYECTOS II\EXPOSICION\expo2_akira\docs\plots\delitos_lima_2024.html",
    full_html=True,
    include_plotlyjs="cdn",
    config={"responsive": True}
)


In [53]:
# Se usará un shapefile para graficar la cantidad de delitos por región
import geopandas as gpd
import matplotlib.pyplot as plt
import matplotlib.colors as mcolors
import matplotlib.cm as cm

# Cargar el shapefile de regiones
ruta_shapefile = r"Z:\06_BASES_DE_DATOS\02_MAPA_DISTRITAL\LIMITE DISTRITAL PERU INEI 2023\Distrital INEI 2023 geogpsperu SuyoPomalia.shp"
gdf_regiones = gpd.read_file(ruta_shapefile)
gdf_regiones.dtypes


UBIGEO          object
CCDD            object
CCPP            object
CCDI            object
DEPARTAMEN      object
PROVINCIA       object
DISTRITO        object
OBJECTID       float64
ESRI_OID       float64
geometry      geometry
dtype: object

In [54]:
gdf_regiones["UBIGEO"] = pd.to_numeric(gdf_regiones["UBIGEO"], errors="coerce")

In [55]:
mapa_delitos_2024 = gdf_regiones.merge(
    df_2024,
    left_on="UBIGEO",
    right_on="UBIGEO_HECHO",
    how="left")
mapa_delitos_2024


UBIGEO CCDD CCPP CCDI DEPARTAMEN    PROVINCIA                DISTRITO  \
0      10101   01   01   01   AMAZONAS  CHACHAPOYAS             CHACHAPOYAS   
1      10102   01   01   02   AMAZONAS  CHACHAPOYAS                ASUNCION   
2      10103   01   01   03   AMAZONAS  CHACHAPOYAS                  BALSAS   
3      10104   01   01   04   AMAZONAS  CHACHAPOYAS                   CHETO   
4      10105   01   01   05   AMAZONAS  CHACHAPOYAS               CHILIQUIN   
...      ...  ...  ...  ...        ...          ...                     ...   
1886  250304   25   03   04    UCAYALI   PADRE ABAD                 NESHUYA   
1887  250305   25   03   05    UCAYALI   PADRE ABAD  ALEXANDER VON HUMBOLDT   
1888  250306   25   03   06    UCAYALI   PADRE ABAD                 HUIPOCA   
1889  250307   25   03   07    UCAYALI   PADRE ABAD                BOQUERON   
1890  250401   25   04   01    UCAYALI        PURUS                   PURUS   

      OBJECTID  ESRI_OID                                           geometry  \
0          1.0       1.0  POLYGON ((-77.8858 -6.1778, -77.88323 -6.17846...   
1          2.0       2.0  POLYGON ((-77.74482 -5.94497, -77.74482 -5.945...   
2          3.0       3.0  POLYGON ((-77.9358 -6.69039, -77.93531 -6.6909...   
3          4.0       4.0  POLYGON ((-77.71486 -6.24598, -77.71485 -6.245...   
4          5.0       5.0  POLYGON ((-77.77405 -5.99598, -77.77328 -5.996...   
...        ...       ...                                                ...   
1886    1887.0    1887.0  POLYGON ((-75.01663 -8.44514, -75.0165 -8.4453...   
1887    1888.0    1888.0  POLYGON ((-75.02136 -8.73948, -75.02136 -8.739...   
1888    1889.0    1889.0  POLYGON ((-75.3844 -8.58229, -75.38423 -8.5825...   
1889    1890.0    1890.0  POLYGON ((-75.77583 -8.91013, -75.77427 -8.910...   
1890    1891.0    1891.0  POLYGON ((-70.50641 -9.42392, -70.50643 -9.424...   

      UBIGEO_HECHO  n_dist_ID_DGC  
0              NaN            NaN  
1              NaN            NaN  
2              NaN            NaN  
3              NaN            NaN  
4              NaN            NaN  
...            ...            ...  
1886           NaN            NaN  
1887           NaN            NaN  
1888           NaN            NaN  
1889           NaN            NaN  
1890           NaN            NaN  

[1891 rows x 12 columns]

In [56]:
lima_delitos_2024 = mapa_delitos_2024[mapa_delitos_2024["UBIGEO"]//100 == 1501].copy()
lima_delitos_2024.isnull().sum()
lima_delitos_2024

UBIGEO CCDD CCPP CCDI DEPARTAMEN PROVINCIA                 DISTRITO  \
1293  150101   15   01   01       LIMA      LIMA                     LIMA   
1294  150102   15   01   02       LIMA      LIMA                    ANCON   
1295  150103   15   01   03       LIMA      LIMA                      ATE   
1296  150104   15   01   04       LIMA      LIMA                 BARRANCO   
1297  150105   15   01   05       LIMA      LIMA                    BREÑA   
1298  150106   15   01   06       LIMA      LIMA               CARABAYLLO   
1299  150107   15   01   07       LIMA      LIMA               CHACLACAYO   
1300  150108   15   01   08       LIMA      LIMA               CHORRILLOS   
1301  150109   15   01   09       LIMA      LIMA              CIENEGUILLA   
1302  150110   15   01   10       LIMA      LIMA                    COMAS   
1303  150111   15   01   11       LIMA      LIMA              EL AGUSTINO   
1304  150112   15   01   12       LIMA      LIMA            INDEPENDENCIA   
1305  150113   15   01   13       LIMA      LIMA              JESUS MARIA   
1306  150114   15   01   14       LIMA      LIMA                LA MOLINA   
1307  150115   15   01   15       LIMA      LIMA              LA VICTORIA   
1308  150116   15   01   16       LIMA      LIMA                    LINCE   
1309  150117   15   01   17       LIMA      LIMA               LOS OLIVOS   
1310  150118   15   01   18       LIMA      LIMA               LURIGANCHO   
1311  150119   15   01   19       LIMA      LIMA                    LURIN   
1312  150120   15   01   20       LIMA      LIMA        MAGDALENA DEL MAR   
1313  150121   15   01   21       LIMA      LIMA             PUEBLO LIBRE   
1314  150122   15   01   22       LIMA      LIMA               MIRAFLORES   
1315  150123   15   01   23       LIMA      LIMA               PACHACAMAC   
1316  150124   15   01   24       LIMA      LIMA                 PUCUSANA   
1317  150125   15   01   25       LIMA      LIMA            PUENTE PIEDRA   
1318  150126   15   01   26       LIMA      LIMA            PUNTA HERMOSA   
1319  150127   15   01   27       LIMA      LIMA              PUNTA NEGRA   
1320  150128   15   01   28       LIMA      LIMA                    RIMAC   
1321  150129   15   01   29       LIMA      LIMA              SAN BARTOLO   
1322  150130   15   01   30       LIMA      LIMA                SAN BORJA   
1323  150131   15   01   31       LIMA      LIMA               SAN ISIDRO   
1324  150132   15   01   32       LIMA      LIMA   SAN JUAN DE LURIGANCHO   
1325  150133   15   01   33       LIMA      LIMA   SAN JUAN DE MIRAFLORES   
1326  150134   15   01   34       LIMA      LIMA                 SAN LUIS   
1327  150135   15   01   35       LIMA      LIMA     SAN MARTIN DE PORRES   
1328  150136   15   01   36       LIMA      LIMA               SAN MIGUEL   
1329  150137   15   01   37       LIMA      LIMA              SANTA ANITA   
1330  150138   15   01   38       LIMA      LIMA      SANTA MARIA DEL MAR   
1331  150139   15   01   39       LIMA      LIMA               SANTA ROSA   
1332  150140   15   01   40       LIMA      LIMA        SANTIAGO DE SURCO   
1333  150141   15   01   41       LIMA      LIMA                SURQUILLO   
1334  150142   15   01   42       LIMA      LIMA        VILLA EL SALVADOR   
1335  150143   15   01   43       LIMA      LIMA  VILLA MARIA DEL TRIUNFO   

      OBJECTID  ESRI_OID                                           geometry  \
1293    1294.0    1294.0  POLYGON ((-77.00972 -12.03083, -77.00921 -12.0...   
1294    1295.0    1295.0  POLYGON ((-77.06652 -11.57251, -77.06614 -11.5...   
1295    1296.0    1296.0  POLYGON ((-76.83689 -11.9937, -76.83517 -11.99...   
1296    1297.0    1297.0  POLYGON ((-77.01948 -12.13061, -77.01933 -12.1...   
1297    1298.0    1298.0  POLYGON ((-77.05335 -12.04917, -77.05332 -12.0...   
1298    1299.0    1299.0  POLYGON ((-76.90215 -11.72887, -76.9013 -11.72...   
1299    1300.0    1300.0  POLYGON ((-76.73089 -11.96185, -76.730

In [66]:
fig2 = px.choropleth_mapbox(
    lima_delitos_2024,
    geojson=lima_delitos_2024.geometry.__geo_interface__,
    locations=lima_delitos_2024.index,
    color="n_dist_ID_DGC",
    color_continuous_scale=px.colors.sequential.Plasma,
    mapbox_style="carto-positron",
    zoom=8,
    height=800,
    center={"lat": -12.046374, "lon": -77.042793},
    opacity=0.5,
    labels={"n_dist_ID_DGC": "Cantidad de Delitos"},
    hover_data={
        "DISTRITO": True,
        "PROVINCIA": True,
        "DEPARTAMEN": True,
        "n_dist_ID_DGC": True
    }
)
fig2.update_layout(
    title="Distritos de Lima Metropolitana - Según delitos reportados en el 2024",
    title_x=0.5,
    plot_bgcolor="#0d1117",
    paper_bgcolor="#0d1117",
    font=dict(color="#c9d1d9"),
    autosize=True,
    height=None,  # ← evita height fijo
    margin=dict(t=40, r=0, l=10, b=0),
)
fig2.show()




C:\Users\SystemPeru\AppData\Local\Temp\ipykernel_9700\3223236875.py:1: DeprecationWarning:

*choropleth_mapbox* is deprecated! Use *choropleth_map* instead. Learn more at: https://plotly.com/python/mapbox-to-maplibre/



In [64]:
fig2.write_html(r"Z:\02_Maestría UNI\I_TALLER DE PROYECTOS II\EXPOSICION\expo2_akira\docs\plots\mapa_delito_lima.html",
    full_html=True,
    include_plotlyjs="cdn",
    config={"responsive": True}
)


In [ ]:
from sklearn.tree import DecisionTreeClassifier
from sklearn import tree
import matplotlib.pyplot as plt
import plotly.graph_objects as go

# Crear un árbol de decisión ficticio para ilustrar el ejemplo
clf = DecisionTreeClassifier()
clf = clf.fit([[0, 0], [1, 1], [0, 1], [1, 0]], [0, 1, 1, 0])

# Nivel 1
fig.add_trace(go.Scatter(
    x=[0.5], y=[1],
    mode='markers+text',
    marker=dict(size=50, color='blue'),
    text=['ÁRBOL DE DECISIÓN: ALTERNATIVA ELEGICA'],
    textposition='top center',
    hoverinfo='text',
))

# Nivel 2
fig.add_trace(go.Scatter(
    x=[0.2, 0.5, 0.8], y=[0.7, 0.7, 0.7],
    mode='markers+text',
    marker=dict(size=40, color='green'),
    text=['Nivel 2 - A', 'Nivel 2 - B', 'Nivel 2 - C'],
    textposition='top center',
    hoverinfo='text',
))

# Nivel 3
fig.add_trace(go.Scatter(
    x=[0.1, 0.3, 0.4, 0.6, 0.7, 0.9], y=[0.4, 0.4, 0.4, 0.4, 0.4, 0.4],
    mode='markers+text',
    marker=dict(size=30, color='orange'),
    text=['Nivel 3 - A1', 'Nivel 3 - A2', 'Nivel 3 - B1', 'Nivel 3 - B2', 'Nivel 3 - C1', 'Nivel 3 - C2'],
    textposition='top center',
    hoverinfo='text',
))

# Conexiones
lines = [
    # Nivel 1 a Nivel 2
    ([0.5, 0.2], [1, 0.7]), ([0.5, 0.5], [1, 0.7]), ([0.5, 0.8], [1, 0.7]),
    # Nivel 2 a Nivel 3
    ([0.2, 0.1], [0.7, 0.4]), ([0.2, 0.3], [0.7, 0.4]),
    ([0.5, 0.4], [0.7, 0.4]), ([0.5, 0.6], [0.7, 0.4]),
    ([0.8, 0.7], [0.7, 0.4]), ([0.8, 0.9], [0.7, 0.4]),
]

for line in lines:
    fig.add_trace(go.Scatter(
        x=line[0], y=line[1],
        mode='lines',
        line=dict(color='gray', width=2),
        hoverinfo='none',
    ))

# Estilo general
fig.update_layout(
    title='Árbol de Decisión Interactivo',
    title_x=0.5,
    xaxis=dict(showgrid=False, zeroline=False, visible=False),
    yaxis=dict(showgrid=False, zeroline=False, visible=False),
    plot_bgcolor='white',
    height=600,
    margin=dict(t=60, r=20, l=20, b=20),
)

# # Exportar a HTML
# fig.write_html(r"Z:\\02_Maestría UNI\\I_TALLER DE PROYECTOS II\\EXPOSICION\\expo2_akira\\docs\\plots\\arbol_interactivo.html",
#     full_html=True,
#     include_plotlyjs="cdn",
#     config={"responsive": True}
# )

fig.show()